# <font color="blue"> Cross-entropy on FrozenLake <font>
 
### grid world
<img src="./image/4/gridworld.png">


#### - 4x4 격자 세계 
#### - 4가지 방향으로 행동 가능 
- 위, 아래, 왼쪽, 오른쪽 


#### - 시작은 항상 격자의 왼쪽 가장 위 
#### - 목표는 격자의 오른쪽 가장 아래 
- 목표에 도달하면 에피소드는 종료되고 보상은 1


#### - 고정된 구멍 존재 
- 구멍에 빠지면 에피소드는 종료되고 얻는 보상은 0 

#### - 미끄러운 세계 (world is slippery) 
- 에이전트의 액션은 항상 예측한대로 나타나지 않음 
    - 33%의 확률로 오른쪽 / 왼쪽으로 미끄러질 수 있음 
    - 예) 에이전트를 왼쪽으로 움직이고 싶을때, 33%의 확률로 왼쪽, 33% 위, 33% 아래 
- 더 복잡한 환경은 과정을 더 어렵게 만듦 

In [1]:
import gym, gym.spaces
from collections import namedtuple
import numpy as np
from tensorboardX import SummaryWriter

import torch
import torch.nn as nn
import torch.optim as optim

In [2]:
HIDDEN_SIZE = 128
BATCH_SIZE = 16
PERCENTILE = 70

## one-hot encoding 작업 

#### - 이산적(discrete) 관찰 
- 관찰은 단지 0~15 의 숫자 
- 관찰은 결국 격자에서 에이전트의 위치 

#### - 이산적 액션 
- 액션은 0~3

#### - 입력과 출력을 벡터로 만들기 위해 one-hot encoding 필요 
- 0 --> 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 

#### - Gym 패키지의 ObservationWrapper 사용하여 DiscreteOneHotWrapper 구현 

#### - 이 외의 코드는 앞서 봤던 CartPole 코드와 모두 동일 
- 환경만 Frozen Lake

In [3]:
# DiscreteOneHotWrapper is son of gym.ObservationWrapper
class DiscreteOneHotWrapper(gym.ObservationWrapper):
    def __init__(self, env):
        super(DiscreteOneHotWrapper, self).__init__(env)
        assert isinstance(env.observation_space, gym.spaces.Discrete)
        
        #gym.spaces.Box(low, high, shape, dtype)
        self.observation_space = gym.spaces.Box(0.0, 1.0, (env.observation_space.n, ), dtype=np.float32)
        
    
    def observation(self, observation):
        res = np.copy(self.observation_space.low) 
        res[observation] = 1.0
        
        return res

In [5]:
class Net(nn.Module):
    def __init__(self, obs_zie, hidden_size, n_actions):
        super(Net, self).__init__()
        
        self.net = nn.Sequential(nn.Linear(obs_size, hidden_size), 
                                 nn.ReLU(),
                                 nn.Linear(hidden_size, n_actions))
    
    def forward(self, x):
        return self.net(x)

In [6]:
Episode = namedtuple('Episode', field_names=['reward', 'steps'])
EpisodeStep = namedtuple('EpisodeStep', field_names=['observation', 'action'])

In [7]:
def iterate_batches(env, ent, batch_size):
    batch = []
    episode_reward = 0.0
    episode_steps = []
    obs = env.reset()
    sm = nn.Softmax(dim=1)
    
    while True :
        """choosing action"""
        obs_v = torch.FloatTensor([obs])
        act_probs_v = sm(net(obs_v))
        act_probs = act_probs_v.data.numpy()[0]
        action = np.random.choice(len(act_probs), p=act_probs)
        
        """step"""
        next_obs, reward, is_done, _ = env.step(action)
        
       # env.render()
        
        """recording"""
        episode_reward += reward 
        episode_steps.append(EpisodeStep(observation=obs, action=action))
        #steping until the pole is fallen
        if is_done :
            batch.append(Episode(reward=episode_reward, steps=episode_steps))
           
            episode_reward = 0.0
            episode_steps = []
            next_obs = env.reset()
            
            if len(batch) == batch_size :
                yield batch
                
                batch = []
        
        obs = next_obs

In [8]:
def filter_batch(batch, percentile):
    rewards = list(map(lambda s : s.reward, batch))
    reward_bound = np.percentile(rewards, percentile)
    reward_mean = float(np.mean(rewards))
    
    train_obs = []
    train_act = []
    
    for example in batch:
        if example.reward < reward_bound:
            continue
            
        train_obs.extend(map(lambda step : step.observation, example.steps))
        train_act.extend(map(lambda step : step.action, example.steps))
        
    train_obs_v = torch.FloatTensor(train_obs)
    train_act_v = torch.LongTensor(train_act)
    
    return train_obs_v, train_act_v, reward_bound, reward_mean 

In [9]:
if __name__ == "__main__":
    env = DiscreteOneHotWrapper(gym.make("FrozenLake-v0"))
    #env = gym.wrappers.Monitor(env, directory="mon", force=True)
    
    obs_size = env.observation_space.shape[0]
    n_actions = env.action_space.n 
    
    net = Net(obs_size, HIDDEN_SIZE, n_actions)
    
    objective = nn.CrossEntropyLoss()
    
    optimizer = optim.Adam(params=net.parameters(), lr=0.01)
    
    writer = SummaryWriter(comment=".frozenlake-naive")
    
    
    for iter_no, batch in enumerate(iterate_batches(env, net, BATCH_SIZE)):
        obs_v, acts_v, reward_b, reward_m = filter_batch(batch, PERCENTILE)
        
        optimizer.zero_grad()
        
        """loss"""
        action_scores_v = net(obs_v)
        loss_v = objective(action_scores_v, acts_v)
        loss_v.backward()
        
        optimizer.step()
        
        print("%d: loss=%.3f, reward_mean=%.1f, reward_bound=%.1f" % 
              (iter_no, loss_v.item(), reward_m, reward_b))
        
        
        writer.add_scalar("loss", loss_v.item(), iter_no)
        writer.add_scalar("reward_bound", reward_b, iter_no)
        writer.add_scalar("reward_mean", reward_m, iter_no)
        
        if reward_m > 0.8 :
            print("Solved!")
            break
            
    writer.close()
    

0: loss=1.381, reward_mean=0.0, reward_bound=0.0
1: loss=1.374, reward_mean=0.0, reward_bound=0.0
2: loss=1.335, reward_mean=0.0, reward_bound=0.0
3: loss=1.351, reward_mean=0.0, reward_bound=0.0
4: loss=1.342, reward_mean=0.0, reward_bound=0.0
5: loss=1.329, reward_mean=0.0, reward_bound=0.0
6: loss=1.343, reward_mean=0.0, reward_bound=0.0
7: loss=1.307, reward_mean=0.1, reward_bound=0.0
8: loss=1.257, reward_mean=0.0, reward_bound=0.0
9: loss=1.314, reward_mean=0.0, reward_bound=0.0
10: loss=1.308, reward_mean=0.0, reward_bound=0.0
11: loss=1.276, reward_mean=0.0, reward_bound=0.0
12: loss=1.295, reward_mean=0.0, reward_bound=0.0
13: loss=1.307, reward_mean=0.1, reward_bound=0.0
14: loss=1.318, reward_mean=0.0, reward_bound=0.0
15: loss=1.259, reward_mean=0.0, reward_bound=0.0
16: loss=1.357, reward_mean=0.0, reward_bound=0.0
17: loss=1.242, reward_mean=0.0, reward_bound=0.0
18: loss=1.259, reward_mean=0.1, reward_bound=0.0
19: loss=1.281, reward_mean=0.0, reward_bound=0.0
20: loss=1

166: loss=0.830, reward_mean=0.1, reward_bound=0.0
167: loss=0.896, reward_mean=0.1, reward_bound=0.0
168: loss=0.804, reward_mean=0.0, reward_bound=0.0
169: loss=0.770, reward_mean=0.0, reward_bound=0.0
170: loss=0.840, reward_mean=0.1, reward_bound=0.0
171: loss=0.719, reward_mean=0.0, reward_bound=0.0
172: loss=0.798, reward_mean=0.1, reward_bound=0.0
173: loss=0.876, reward_mean=0.0, reward_bound=0.0
174: loss=0.712, reward_mean=0.0, reward_bound=0.0
175: loss=0.820, reward_mean=0.0, reward_bound=0.0
176: loss=0.754, reward_mean=0.0, reward_bound=0.0
177: loss=0.807, reward_mean=0.0, reward_bound=0.0
178: loss=0.690, reward_mean=0.0, reward_bound=0.0
179: loss=0.812, reward_mean=0.0, reward_bound=0.0
180: loss=0.680, reward_mean=0.0, reward_bound=0.0
181: loss=1.012, reward_mean=0.0, reward_bound=0.0
182: loss=0.776, reward_mean=0.0, reward_bound=0.0
183: loss=1.043, reward_mean=0.0, reward_bound=0.0
184: loss=0.865, reward_mean=0.0, reward_bound=0.0
185: loss=0.911, reward_mean=0.

329: loss=0.538, reward_mean=0.0, reward_bound=0.0
330: loss=0.403, reward_mean=0.0, reward_bound=0.0
331: loss=0.459, reward_mean=0.0, reward_bound=0.0
332: loss=0.440, reward_mean=0.0, reward_bound=0.0
333: loss=0.522, reward_mean=0.0, reward_bound=0.0
334: loss=0.472, reward_mean=0.0, reward_bound=0.0
335: loss=0.420, reward_mean=0.0, reward_bound=0.0
336: loss=0.428, reward_mean=0.0, reward_bound=0.0
337: loss=0.459, reward_mean=0.0, reward_bound=0.0
338: loss=0.512, reward_mean=0.0, reward_bound=0.0
339: loss=0.382, reward_mean=0.0, reward_bound=0.0
340: loss=0.401, reward_mean=0.0, reward_bound=0.0
341: loss=0.375, reward_mean=0.0, reward_bound=0.0
342: loss=0.374, reward_mean=0.1, reward_bound=0.0
343: loss=0.395, reward_mean=0.0, reward_bound=0.0
344: loss=0.338, reward_mean=0.0, reward_bound=0.0
345: loss=0.394, reward_mean=0.0, reward_bound=0.0
346: loss=0.397, reward_mean=0.0, reward_bound=0.0
347: loss=0.397, reward_mean=0.0, reward_bound=0.0
348: loss=0.439, reward_mean=0.

490: loss=0.553, reward_mean=0.0, reward_bound=0.0
491: loss=0.585, reward_mean=0.0, reward_bound=0.0
492: loss=0.590, reward_mean=0.0, reward_bound=0.0
493: loss=0.600, reward_mean=0.0, reward_bound=0.0
494: loss=0.605, reward_mean=0.0, reward_bound=0.0
495: loss=0.599, reward_mean=0.0, reward_bound=0.0
496: loss=0.554, reward_mean=0.0, reward_bound=0.0
497: loss=0.619, reward_mean=0.0, reward_bound=0.0
498: loss=0.592, reward_mean=0.0, reward_bound=0.0
499: loss=0.667, reward_mean=0.0, reward_bound=0.0
500: loss=0.727, reward_mean=0.0, reward_bound=0.0
501: loss=0.602, reward_mean=0.0, reward_bound=0.0
502: loss=0.609, reward_mean=0.0, reward_bound=0.0
503: loss=0.643, reward_mean=0.0, reward_bound=0.0
504: loss=0.683, reward_mean=0.0, reward_bound=0.0
505: loss=0.634, reward_mean=0.0, reward_bound=0.0
506: loss=0.638, reward_mean=0.0, reward_bound=0.0
507: loss=0.597, reward_mean=0.0, reward_bound=0.0
508: loss=0.613, reward_mean=0.0, reward_bound=0.0
509: loss=0.617, reward_mean=0.

653: loss=0.162, reward_mean=0.0, reward_bound=0.0
654: loss=0.121, reward_mean=0.0, reward_bound=0.0
655: loss=0.112, reward_mean=0.0, reward_bound=0.0
656: loss=0.089, reward_mean=0.0, reward_bound=0.0
657: loss=0.155, reward_mean=0.1, reward_bound=0.0
658: loss=0.215, reward_mean=0.1, reward_bound=0.0
659: loss=0.239, reward_mean=0.1, reward_bound=0.0
660: loss=0.058, reward_mean=0.0, reward_bound=0.0
661: loss=0.221, reward_mean=0.0, reward_bound=0.0
662: loss=0.119, reward_mean=0.1, reward_bound=0.0
663: loss=0.169, reward_mean=0.0, reward_bound=0.0
664: loss=0.024, reward_mean=0.0, reward_bound=0.0
665: loss=0.222, reward_mean=0.0, reward_bound=0.0
666: loss=0.136, reward_mean=0.0, reward_bound=0.0
667: loss=0.117, reward_mean=0.0, reward_bound=0.0
668: loss=0.230, reward_mean=0.1, reward_bound=0.0
669: loss=0.199, reward_mean=0.1, reward_bound=0.0
670: loss=0.028, reward_mean=0.1, reward_bound=0.0
671: loss=0.066, reward_mean=0.0, reward_bound=0.0
672: loss=0.175, reward_mean=0.

...

139201: loss=0.000, reward_mean=0.1, reward_bound=0.0
139202: loss=0.000, reward_mean=0.0, reward_bound=0.0
139203: loss=0.000, reward_mean=0.0, reward_bound=0.0
139204: loss=0.000, reward_mean=0.1, reward_bound=0.0
139205: loss=0.000, reward_mean=0.0, reward_bound=0.0
139206: loss=0.000, reward_mean=0.1, reward_bound=0.0
139207: loss=0.000, reward_mean=0.1, reward_bound=0.0
139208: loss=0.000, reward_mean=0.0, reward_bound=0.0
139209: loss=0.000, reward_mean=0.0, reward_bound=0.0
139210: loss=0.000, reward_mean=0.0, reward_bound=0.0
139211: loss=0.000, reward_mean=0.0, reward_bound=0.0
139212: loss=0.000, reward_mean=0.1, reward_bound=0.0
139213: loss=0.000, reward_mean=0.0, reward_bound=0.0
139214: loss=0.000, reward_mean=0.1, reward_bound=0.0
139215: loss=0.000, reward_mean=0.1, reward_bound=0.0
139216: loss=0.000, reward_mean=0.1, reward_bound=0.0
139217: loss=0.000, reward_mean=0.1, reward_bound=0.0
139218: loss=0.000, reward_mean=0.0, reward_bound=0.0
139219: loss=0.000, reward_m

139355: loss=0.000, reward_mean=0.0, reward_bound=0.0
139356: loss=0.000, reward_mean=0.0, reward_bound=0.0
139357: loss=0.000, reward_mean=0.2, reward_bound=0.0
139358: loss=0.000, reward_mean=0.1, reward_bound=0.0
139359: loss=0.000, reward_mean=0.1, reward_bound=0.0
139360: loss=0.000, reward_mean=0.1, reward_bound=0.0
139361: loss=0.000, reward_mean=0.1, reward_bound=0.0
139362: loss=0.000, reward_mean=0.0, reward_bound=0.0
139363: loss=0.000, reward_mean=0.0, reward_bound=0.0
139364: loss=0.000, reward_mean=0.0, reward_bound=0.0
139365: loss=0.000, reward_mean=0.1, reward_bound=0.0
139366: loss=0.000, reward_mean=0.0, reward_bound=0.0
139367: loss=0.000, reward_mean=0.0, reward_bound=0.0
139368: loss=0.000, reward_mean=0.1, reward_bound=0.0
139369: loss=0.000, reward_mean=0.1, reward_bound=0.0
139370: loss=0.000, reward_mean=0.1, reward_bound=0.0
139371: loss=0.000, reward_mean=0.0, reward_bound=0.0
139372: loss=0.000, reward_mean=0.2, reward_bound=0.0
139373: loss=0.000, reward_m

139514: loss=0.000, reward_mean=0.1, reward_bound=0.0
139515: loss=0.000, reward_mean=0.0, reward_bound=0.0
139516: loss=0.000, reward_mean=0.1, reward_bound=0.0
139517: loss=0.000, reward_mean=0.1, reward_bound=0.0
139518: loss=0.000, reward_mean=0.1, reward_bound=0.0
139519: loss=0.000, reward_mean=0.0, reward_bound=0.0
139520: loss=0.000, reward_mean=0.0, reward_bound=0.0
139521: loss=0.000, reward_mean=0.1, reward_bound=0.0
139522: loss=0.000, reward_mean=0.1, reward_bound=0.0
139523: loss=0.000, reward_mean=0.0, reward_bound=0.0
139524: loss=0.000, reward_mean=0.1, reward_bound=0.0
139525: loss=0.000, reward_mean=0.0, reward_bound=0.0
139526: loss=0.000, reward_mean=0.1, reward_bound=0.0
139527: loss=0.000, reward_mean=0.1, reward_bound=0.0
139528: loss=0.000, reward_mean=0.1, reward_bound=0.0
139529: loss=0.000, reward_mean=0.0, reward_bound=0.0
139530: loss=0.000, reward_mean=0.0, reward_bound=0.0
139531: loss=0.000, reward_mean=0.0, reward_bound=0.0
139532: loss=0.000, reward_m

139666: loss=0.000, reward_mean=0.0, reward_bound=0.0
139667: loss=0.000, reward_mean=0.1, reward_bound=0.0
139668: loss=0.000, reward_mean=0.1, reward_bound=0.0
139669: loss=0.000, reward_mean=0.1, reward_bound=0.0
139670: loss=0.000, reward_mean=0.0, reward_bound=0.0
139671: loss=0.000, reward_mean=0.1, reward_bound=0.0
139672: loss=0.000, reward_mean=0.1, reward_bound=0.0
139673: loss=0.000, reward_mean=0.0, reward_bound=0.0
139674: loss=0.000, reward_mean=0.0, reward_bound=0.0
139675: loss=0.000, reward_mean=0.1, reward_bound=0.0
139676: loss=0.000, reward_mean=0.1, reward_bound=0.0
139677: loss=0.000, reward_mean=0.0, reward_bound=0.0
139678: loss=0.000, reward_mean=0.1, reward_bound=0.0
139679: loss=0.000, reward_mean=0.1, reward_bound=0.0
139680: loss=0.000, reward_mean=0.1, reward_bound=0.0
139681: loss=0.000, reward_mean=0.1, reward_bound=0.0
139682: loss=0.000, reward_mean=0.1, reward_bound=0.0
139683: loss=0.000, reward_mean=0.0, reward_bound=0.0
139684: loss=0.000, reward_m

KeyboardInterrupt: 

## 결과 
<img src ="./image/4/t-2.png">

#### 시간이 지나도 성능이 좋아지지 않음 


### - 보상 구조 
#### - CartPole 환경, 환경의 모든 단계에서 막대가 떨어질 때까지 보상 1.0을 줌 
- 더 오래 막대기를 유지한 에이전트가 더 높은 보상을 얻음 
- 에이전트의 무작위성으로 인해 꽤나 각 에피소드의 보상은 정규분포를 따름 

<img src = "./image/4/distribution.png">

- 이후 보상경계를 선택하여 덜 성공적인 에피소드를 제외하고 더 나은 에피소드를 반복하도록 학습 
    

#### - FrozenLake 환경, 목적지에 도달해야만 보상 1.0을 줌 
- 어떤 에피소드가 좋은 것인지 알 수 없음 
- 어떤 방법으로 목적지에 도달했는지 알 수 없음 
- 에피소드의 보상의 분포는 애매해짐 

<img src="./image/4/f_distribution.png">
   
- 0 (실패) / 1 (성공) 
- 엘리트 에피소드를 걸러내는 것이 잘못되었고 좋지 않은 에피소드를 학습하게 됨 
- 그러므로, 학습이 실패함

## Cross-entropy 방법의 한계 
#### - 학습에 있어서, 에피소드는 유한하고 가급적 짧아야 함 
#### - 에피소드의 총 보상은 좋은 에피소드와 나쁜 에피소드를 구분할 수 있을만큼 충분한 변동성이 있어야 함 
#### - 에이전트가 성공할지 실패할지에 대해 중간에 알 수 없음 
#### - 이러한 한계들은 앞으로 배울 다른 방법들에의해 다뤄질 수 있음 


